In [ ]:
import gradio as gr
import plotly.graph_objects as go
from datasets import load_dataset

# Load dataset once
dataset = load_dataset("gradio/NYC-Airbnb-Open-Data", split="train")
df = dataset.to_pandas()

def filter_map(min_price, max_price, boroughs):
    # Handle empty boroughs list
    if not boroughs:
        boroughs = ["Queens", "Brooklyn", "Manhattan", "Bronx", "Staten Island"]
    
    # Filter dataframe
    filtered_df = df[(df['neighbourhood_group'].isin(boroughs)) &
                    (df['price'] > min_price) & (df['price'] < max_price)]
    
    # Handle empty results
    if filtered_df.empty:
        # Return empty map
        fig = go.Figure()
        fig.update_layout(
            title="No properties found with current filters",
            mapbox_style="open-street-map",
            mapbox=dict(
                center=go.layout.mapbox.Center(lat=40.67, lon=-73.90),
                zoom=9
            ),
        )
        return fig
    
    # Prepare data for map
    names = filtered_df["name"].tolist()
    prices = filtered_df["price"].tolist()
    text_list = [(names[i], prices[i]) for i in range(len(names))]
    
    # Create the map
    fig = go.Figure(go.Scattermapbox(
        customdata=text_list,
        lat=filtered_df['latitude'].tolist(),
        lon=filtered_df['longitude'].tolist(),
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=6,
            color=filtered_df['price'],
            colorscale='Viridis',
            showscale=True,
            colorbar=dict(
                title="Price ($)",
                titleside="top",
                x=0.02,  # Move to left side
                y=0.98,  # Move to top
                len=0.3,  # Make it shorter
                thickness=15,  # Make it thinner
                xanchor="left",
                yanchor="top"
            )
        ),
        hoverinfo="text",
        hovertemplate='<b>Name</b>: %{customdata[0]}<br><b>Price</b>: $%{customdata[1]}<extra></extra>'
    ))

    fig.update_layout(
        title=f"NYC Airbnb Properties ({len(filtered_df)} properties)",
        mapbox_style="open-street-map",
        hovermode='closest',
        mapbox=dict(
            bearing=0,
            center=go.layout.mapbox.Center(lat=40.67, lon=-73.90),
            pitch=0,
            zoom=9
        ),
        height=600
    )
    
    return fig

In [6]:
import plotly.graph_objects as go

# Define sample data (replace with your actual filtered data)
new_df = df  # Using first 100 rows as example
names = new_df["name"].tolist()
prices = new_df["price"].tolist()
text_list = [(names[i], prices[i]) for i in range(len(names))]

fig = go.Figure(go.Scattermapbox(
            customdata=text_list,
            lat=new_df['latitude'].tolist(),
            lon=new_df['longitude'].tolist(),
            mode='markers',
            marker=go.scattermapbox.Marker(
                size=6
            ),
            hoverinfo="text",
            hovertemplate='<b>Name</b>: %{customdata[0]}<br><b>Price</b>: $%{customdata[1]}'
        ))

fig.update_layout(
    mapbox_style="open-street-map",
    hovermode='closest',
    mapbox=dict(
        bearing=0,
        center=go.layout.mapbox.Center(
            lat=40.67,
            lon=-73.90
        ),
        pitch=0,
        zoom=9
    ),
)

/var/folders/sb/fx7gkfvd347dl53rhgbljz_80000gp/T/ipykernel_94870/2144296762.py:9: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [7]:
# Get price range for slider defaults
min_price = int(df['price'].min())
max_price = int(df['price'].max())
print(f"Price range: ${min_price} - ${max_price}")

# Create interactive interface
with gr.Blocks(title="NYC Airbnb Map Explorer") as demo:
    gr.Markdown("# NYC Airbnb Interactive Map")
    gr.Markdown("Filter properties by price range and borough to explore NYC Airbnb listings")
    
    with gr.Row():
        with gr.Column(scale=1):
            gr.Markdown("### Filters")
            
            # Price range slider
            price_range = gr.Slider(
                minimum=min_price,
                maximum=min(max_price, 1000),  # Cap at $1000 for better UX
                value=500,
                step=10,
                label="Maximum Price ($)",
                info="Filter properties under this price"
            )
            
            min_price_slider = gr.Slider(
                minimum=min_price,
                maximum=500,
                value=50,
                step=10,
                label="Minimum Price ($)",
                info="Filter properties above this price"
            )
            
            # Borough selection
            borough_choices = ["Queens", "Brooklyn", "Manhattan", "Bronx", "Staten Island"]
            boroughs = gr.CheckboxGroup(
                choices=borough_choices,
                value=borough_choices,  # All selected by default
                label="Boroughs",
                info="Select which boroughs to include"
            )
            
        with gr.Column(scale=3):
            # Map output
            map_plot = gr.Plot(label="Interactive Map")
    
    # Update map when filters change
    def update_map(min_price_val, max_price_val, selected_boroughs):
        return filter_map(min_price_val, max_price_val, selected_boroughs)
    
    # Connect inputs to the map update
    inputs = [min_price_slider, price_range, boroughs]
    for input_component in inputs:
        input_component.change(
            fn=update_map,
            inputs=inputs,
            outputs=map_plot
        )
    
    # Load initial map
    demo.load(
        fn=lambda: filter_map(50, 500, borough_choices),
        outputs=map_plot
    )

# Launch the interface
demo.launch(share=True, debug=True)


Price range: $0 - $10000
* Running on local URL:  http://127.0.0.1:7861
* Running on public URL: https://2f62ef9f2672b8b6d3.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


/var/folders/sb/fx7gkfvd347dl53rhgbljz_80000gp/T/ipykernel_94870/283556685.py:38: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://2f62ef9f2672b8b6d3.gradio.live


In [10]:
import gradio as gr
import matplotlib.pyplot as plt

def create_plot():
    fig, ax = plt.subplots()
    ax.plot([1, 2, 3], [1, 4, 2])
    return fig

interface = gr.Interface(fn=create_plot, inputs=[], outputs=gr.Plot())
interface.launch()  # This opens the web interface

* Running on local URL:  http://127.0.0.1:7861

To create a public link, set `share=True` in `launch()`.


Created dataset file at: .gradio/flagged/dataset2.csv


In [12]:
import gradio as gr
import matplotlib.pyplot as plt

def create_plot():
    fig, ax = plt.subplots()
    ax.plot([1, 2, 3], [1, 4, 2])
    return fig

with gr.Blocks() as demo:
    plot_output = gr.Plot()
    gr.Button("Generate Plot").click(create_plot, outputs=plot_output)

demo.launch()

* Running on local URL:  http://127.0.0.1:7862

To create a public link, set `share=True` in `launch()`.
